# Synthetic population generation for Beijing

The demo shows how you can generate the synthetic population of Beijing using SyntheticPopulation.jl package.

## 1. Include SyntheticPopulation package

In [2]:
include("../src/SyntheticPopulation.jl")

using PyCall
using Colors
folium = pyimport("folium")

PyObject <module 'folium' from '/Users/marcinzurek/.julia/conda/3/x86_64/lib/python3.10/site-packages/folium/__init__.py'>

## 2. Provide input data for individuals and households

For the purpose of this demo, we are using data from:
- Beijing Statistical Yearbook: https://nj.tjj.beijing.gov.cn/nj/main/2021-tjnj/zk/indexeh.htm 
- China Statistical Yearbook: http://www.stats.gov.cn/sj/ndsj/2019/indexeh.htm

The data is input manually in a form of Julia DataFrame. We are using the following tables:
- For attributes of individuals:
    - 3-6 PERMANENT POPULATION BY AGE COMPOSITION (2020)
    - 2-13 Population by Sex, Marital Status and Region (2018)
- For attributes of households:
    - 3-8 FAMILY SIZE OF PERMANENT POPULATION (2020)
    - 5-5 PER CAPITA DISPOSABLE INCOME OF RESIDENTS OF THE WHOLE CITY (BY INCOME LEVEL) (2015-2020)
    
Because of large population of Beijing, the data is scales by 0.1% to decrease computational costs.

Each of dataframes provides information about the distribution of population. We can only access marginal distributions of attributes (e.g. population by age and sex).

In [3]:
#each individual and each household represent 1000 individuals or households
SCALE = 0.001 

0.001

In [4]:
#all values are based on China census data
individual_popoulation_size = 21890000

#individuals
marginal_ind_age_sex = DataFrame(
    sex = repeat(['M', 'F'], 18),
    age = repeat(2:5:87, inner = 2), 
    population = SCALE .* 10000 .* [52.6, 49.0, 48.5, 44.8, 33.6, 30.6, 34.6, 28.8, 71.6, 63.4, 99.6, 90.9, 130.9, 119.4, 110.8, 103.5, 83.8, 76.4, 84.2, 77.7, 84.2, 77.8, 82.8, 79.9, 67.7, 71.0, 56.9, 62.6, 31.5, 35.3, 18.5, 23.0, 15.2, 19.7, 12.5, 16.0]
    )

marginal_ind_sex_maritalstatus = DataFrame(
    sex = repeat(['M', 'F'], 4), 
    maritalstatus = repeat(["Never_married", "Married", "Divorced", "Widowed"], inner = 2), 
    population = SCALE .* [1679, 1611, 5859, 5774, 140, 206, 128, 426] ./ 0.00082
    )

marginal_ind_income = DataFrame(
    income = [25394, 44855, 63969, 88026, 145915], 
    population = repeat([individual_popoulation_size * SCALE / 5], 5)
    )

#households
household_total_population = 8230000
marginal_hh_size = DataFrame(
    hh_size = [1,2,3,4,5],
    population = Int.(round.(SCALE * household_total_population .* [0.299, 0.331, 0.217, 0.09, 0.063]))
    )


5×2 DataFrame
 Row │ hh_size  population 
     │ Int64    Int64      
─────┼─────────────────────
   1 │       1        2461
   2 │       2        2724
   3 │       3        1786
   4 │       4         741
   5 │       5         518

## 3. Generate data about population in Beijing's districts.

Next, we generate a Julia DataFrame which presents population breakdown per each district. This consists of 2 steps:
1. First, we download the distrct boundaries from https://osm-boundaries.com/Map and save into Julia DataFrame.
2. Then, we manually add a column with population for each district, based on Beijing Statistical Yearbook (table 3-4 TOTAL NUMBER AND DENSITY OF PERMANENT POPULATION (BY DISTRICT) (2020))

In [28]:
#areas
URL = "https://osm-boundaries.com/Download/Submit?apiKey=87100809b4085adb58139419c141e5a1&db=osm20230102&osmIds=-2988894,-2988933,-2988895,-288600,-2988896,-2988946,-5505984,-2988897,-2988898,-2988899,-2988900,-5505985,-2988901,-2988902,-568660,-2988903&format=GeoJSON&srid=4326"
areas = generate_areas_dataframe_from_url(URL)

#aggregated_areas - population referenced from https://nj.tjj.beijing.gov.cn/nj/main/2021-tjnj/zk/indexeh.htm
aggregated_areas = copy(areas)
aggregated_areas.:population = SCALE .* 10000 .* [56.8, 313.2, 201.9, 345.1, 34.6, 184.0, 132.4, 45.7, 52.8, 39.3, 44.1, 131.3, 199.4, 226.9, 110.6, 70.9]
aggregated_areas

File downloaded. Unzipping file...
File saved at 

/Users/marcinzurek/Desktop/Studia/Research/SyntheticPopulation/notebooks/file.geojson


16×4 DataFrame
 Row │ id     geometry      name                  population 
     │ Int64  Geometry      String                Float64    
─────┼───────────────────────────────────────────────────────
   1 │     1  Polygon       Shijingshan District       568.0
   2 │     2  Polygon       Haidian District          3132.0
   3 │     3  Polygon       Fengtai District          2019.0
   4 │     4  MultiPolygon  Chaoyang District         3451.0
   5 │     5  Polygon       Yanqing District           346.0
   6 │     6  Polygon       Tongzhou District         1840.0
   7 │     7  Polygon       Shunyi District           1324.0
   8 │     8  Polygon       Pinggu District            457.0
   9 │     9  Polygon       Miyun District             528.0
  10 │    10  Polygon       Mentougou District         393.0
  11 │    11  Polygon       Huairou District           441.0
  12 │    12  Polygon       Fangshan District         1313.0
  13 │    13  Polygon       Daxing District           1994.0
  14 │    14  Polygon       Changping District        2269.0
  15 │    15  Polygon       Xicheng District          1106.0
  16 │    16  Polygon       Dongcheng District         709.0

## 4. Merge marginal distributions to obtain joint distributions for multiple attributes

As the next step, we merge marginal distributions of attributes of individuals to obtain join distributions for attribute combinations. This is done using a recursive algorithm that leverages Iterative Proportional Fitting Method proposed by Guo, Bhat, 2007 [1].
In addition, our algorithm is improved because it can be configured with a JSON file to provide more flexibility. This  approach is insipired by Ponge, Enbergs et al. 2021. The configuration documentation is described elsewhere.

[1] Guo, J. Y., & Bhat, C. R. (2007). Population synthesis for microsimulating travel behavior. Transportation Research Record, 2014(1), 92-101.  
[2] Ponge, J., Enbergs, M., Schüngel, M., Hellingrath, B., Karch, A., & Ludwig, S. (2021, December). Generating synthetic populations based on german census data. In 2021 Winter Simulation Conference (WSC) (pp. 1-12). IEEE.

In [6]:
aggregated_individuals = generate_joint_distribution(marginal_ind_sex_maritalstatus, marginal_ind_age_sex, marginal_ind_income, config_file = "config_file.json")

┌ Info: Inconsistent target margins, converting `X` and `mar` to proportions. Margin totals: [9777, 10698]
└ @ ProportionalFitting /Users/marcinzurek/.julia/packages/ProportionalFitting/gNJEu/src/ipf.jl:61
┌ Info: Converged in 1 iterations.
└ @ ProportionalFitting /Users/marcinzurek/.julia/packages/ProportionalFitting/gNJEu/src/ipf.jl:130


┌ Info: Inconsistent target margins, converting `X` and `mar` to proportions. Margin totals: [9520, 11195]
└ @ ProportionalFitting /Users/marcinzurek/.julia/packages/ProportionalFitting/gNJEu/src/ipf.jl:61
┌ Info: Converged in 1 iterations.
└ @ ProportionalFitting /Users/marcinzurek/.julia/packages/ProportionalFitting/gNJEu/src/ipf.jl:130


┌ Info: Inconsistent target margins, converting `X` and `mar` to proportions. Margin totals: [21893, 21890]
└ @ ProportionalFitting /Users/marcinzurek/.julia/packages/ProportionalFitting/gNJEu/src/ipf.jl:61
┌ Info: Converged in 1 iterations.
└ @ ProportionalFitting /Users/marcinzurek/.julia/packages/ProportionalFitting/gNJEu/src/ipf.jl:130


600×6 DataFrame
 Row │ id     maritalstatus  sex    age     income  population 
     │ Int64  String?        Char?  Int64?  Int64?  Int64      
─────┼─────────────────────────────────────────────────────────
   1 │     1  missing        F           2   25394          99
   2 │     2  missing        M           2   25394         106
   3 │     3  missing        F           7   25394          90
   4 │     4  missing        M           7   25394          98
   5 │     5  missing        F          12   25394          61
   6 │     6  missing        M          12   25394          66
   7 │     7  missing        F          17   25394          57
   8 │     8  missing        M          17   25394          69
  ⋮  │   ⋮          ⋮          ⋮      ⋮       ⋮         ⋮
 594 │   594  Married        F          87  145915          23
 595 │   595  Never_married  F          87  145915           6
 596 │   596  Widowed        F          87  145915           2
 597 │   597  Divorced       M          87  145915           0
 598 │   598  Married        M          87  145915          19
 599 │   599  Never_married  M          87  145915           5
 600 │   600  Widowed        M          87  145915           0
                                               585 rows omitted

We do the same for a dataframe with households to generate households pool.

In [7]:
aggregated_households = generate_joint_distribution(marginal_hh_size)

5×3 DataFrame
 Row │ id     hh_size  population 
     │ Int64  Int64    Int64      
─────┼────────────────────────────
   1 │     1        1        2461
   2 │     2        2        2724
   3 │     3        3        1786
   4 │     4        4         741
   5 │     5        5         518

## 5. Assign individuals to households

Once the individual pool and household pool is generated, we assign individuals to households. The individuals are assigned to households based on the following rules:
1. Each household consists of household head.
2. If household size is 2, then we draw a partner of opposite gender aged +/- 5 years from household head.
3. If houhsehold size is 3-5, we fill the rest of household spots with children. Age difference between parents and child is between 15 and 40.

In [14]:
disaggregated_households, unassigned1 = assign_individuals_to_households(aggregated_individuals, aggregated_households, return_unassigned = true)
disaggregated_households

Total number of individuals: 21890
Total number of households: 8230
Allocation started... 


Progress:   1%|▋                                        |  ETA: 0:00:07

Progress:   3%|█▏                                       |  ETA: 0:00:08

Progress:   4%|█▋                                       |  ETA: 0:00:08

Progress:   5%|██▏                                      |  ETA: 0:00:08

...

Progress:  91%|█████████████████████████████████████▌   |  ETA: 0:00:01

Progress:  94%|██████████████████████████████████████▌  |  ETA: 0:00:00

Progress: 100%|█████████████████████████████████████████| Time: 0:00:06



---------------
There are no available children! 
---------------
Allocated 82.0% individuals.
Allocated 95.0% households.


8230×8 DataFrame
  Row │ id     hh_attr_id  individuals_allocated  head_id  partner_id  child1_ ⋯
      │ Int64  Int64       Bool                   Int64    Int64       Int64   ⋯
──────┼─────────────────────────────────────────────────────────────────────────
    1 │     1           1                  false        0           0          ⋯
    2 │     2           1                   true      463           0
    3 │     3           1                   true      499           0
    4 │     4           1                   true      275           0
    5 │     5           1                   true      111           0          ⋯
    6 │     6           1                   true       87           0
    7 │     7           1                   true      295           0
    8 │     8           1                   true      507           0
  ⋮   │   ⋮        ⋮                 ⋮               ⋮         ⋮           ⋮   ⋱
 8224 │  8224           5                   true      378          46        1 ⋯
 8225 │  8225           5                   true      510         386
 8226 │  8226           5                   true      538         262        4
 8227 │  8227           5                   true       62         442        1
 8228 │  8228           5                   true      410          46        1 ⋯
 8229 │  8229           5                   true      390          18        4
 8230 │  8230           5                   true       70         178
                                                 3 columns and 8215 rows omitted

## 6. Assigning geographical coordinates for households.

Once each household is filled with individuals of certain type, we assign coordinates for each household. This is done in 2 steps:
1. We draw a district for each of the households.
2. We draw random coordinates that are within the polygon that represents district area. 

In [15]:
disaggregated_households, unassigned2 = assign_areas_to_households!(disaggregated_households, aggregated_households, aggregated_areas, return_unassigned = true)
disaggregated_households

Assigning coordinates to households...


Progress:   0%|▏                                        |  ETA: 0:00:41

Progress:   1%|▎                                        |  ETA: 0:00:41

Progress:   1%|▍                                        |  ETA: 0:00:46

Progress:   1%|▌                                        |  ETA: 0:00:47

...

Progress:  99%|████████████████████████████████████████▊|  ETA: 0:00:00

Progress: 100%|████████████████████████████████████████▉|  ETA: 0:00:00

Progress: 100%|█████████████████████████████████████████|  ETA: 0:00:00

Progress: 100%|█████████████████████████████████████████| Time: 0:00:29


8230×11 DataFrame
  Row │ id     hh_attr_id  individuals_allocated  head_id  partner_id  child1_ ⋯
      │ Int64  Int64       Bool                   Int64    Int64       Int64   ⋯
──────┼─────────────────────────────────────────────────────────────────────────
    1 │     1           1                  false        0           0          ⋯
    2 │     2           1                   true      463           0
    3 │     3           1                   true      499           0
    4 │     4           1                   true      275           0
    5 │     5           1                   true      111           0          ⋯
    6 │     6           1                   true       87           0
    7 │     7           1                   true      295           0
    8 │     8           1                   true      507           0
  ⋮   │   ⋮        ⋮                 ⋮               ⋮         ⋮           ⋮   ⋱
 8224 │  8224           5                   true      378          46        1 ⋯
 8225 │  8225           5                   true      510         386
 8226 │  8226           5                   true      538         262        4
 8227 │  8227           5                   true       62         442        1
 8228 │  8228           5                   true      410          46        1 ⋯
 8229 │  8229           5                   true      390          18        4
 8230 │  8230           5                   true       70         178
                                                 6 columns and 8215 rows omitted

## 7. Visualisation

In the dataframe `disaggregated_households` each row represents one household. For each household we assigned some household members, each of them being characterized by a set of attributes. Also, each household has coordinates that show the location of the household.

Let's visualise it:

In [12]:
m = folium.Map(location = [disaggregated_households.lat[1], disaggregated_households.lon[1]], zoom_start=11)
i = 1
for area in unique(disaggregated_households.area_id)
    colrs = distinguishable_colors(length(unique(disaggregated_households.area_id)), [RGB(1,0.6,0.5)])
    hh_color = "#$(hex(colrs[i]))"
    i += 1
    area  = filter(row -> row.area_id == area, disaggregated_households)
    for i in 1:nrow(area)
        folium.Circle(
            location = (area.lat[i], area.lon[i]),
            radius = 100,
            color = hh_color,
            fill = false,
            fill_color = hh_color
        ).add_to(m)
    end
end
m

PyObject <folium.folium.Map object at 0x1124fbc10>

## 8. Analysis of the unassigned households, individuals and areas.

We already checked that 95% of households and 82% of individuals were used in the process of allocating individuals to households. We can further examine the results.

The algorithm stopped because there were no more available children. However one can see that 117 1-person and 145 2-people households are still available for allocation with adult individuals.  

This can be improved by applying combinatorial optimization approach which is an idea for further development of this package.

In [16]:
unassigned1["unassigned_individuals"]

465×6 DataFrame
 Row │ id     maritalstatus  sex    age     income  population 
     │ Int64  String?        Char?  Int64?  Int64?  Int64      
─────┼─────────────────────────────────────────────────────────
   1 │    17  Divorced       F          27   25394           3
   2 │    18  Married        F          27   25394          17
   3 │    19  Never_married  F          27   25394          11
   4 │    20  Widowed        F          27   25394           6
   5 │    21  Divorced       M          27   25394           1
   6 │    22  Married        M          27   25394          28
   7 │    23  Never_married  M          27   25394          13
   8 │    24  Widowed        M          27   25394           2
  ⋮  │   ⋮          ⋮          ⋮      ⋮       ⋮         ⋮
 459 │   591  Never_married  M          82  145915           4
 460 │   593  Divorced       F          87  145915           1
 461 │   594  Married        F          87  145915           3
 462 │   595  Never_married  F          87  145915           3
 463 │   596  Widowed        F          87  145915           1
 464 │   598  Married        M          87  145915           5
 465 │   599  Never_married  M          87  145915           3
                                               450 rows omitted

In [17]:
unassigned1["unassigned_households"]

5×3 DataFrame
 Row │ id     hh_size  population 
     │ Int64  Int64    Int64      
─────┼────────────────────────────
   1 │     1        1         117
   2 │     2        2         145
   3 │     3        3          86
   4 │     4        4          41
   5 │     5        5          26

Now let's examine the results of allocation of coordinates to households. First, we can see that to all of the available households some coordinates were allocated.

Second, we can verify that the total population in each district did not match the target population for those districts.

In [19]:
unassigned2["disaggregated_unassigned_households"]

0×12 DataFrame
 Row │ id     hh_attr_id  individuals_allocated  head_id  partner_id  child1_i ⋯
     │ Int64  Int64       Bool                   Int64    Int64       Int64    ⋯
─────┴──────────────────────────────────────────────────────────────────────────
                                                               7 columns omitted

In [20]:
unassigned2["unassigned_areas"]

16×4 DataFrame
 Row │ id     geometry      name                  population 
     │ Int64  Geometry      String                Int64      
─────┼───────────────────────────────────────────────────────
   1 │     1  Polygon       Shijingshan District         102
   2 │     2  Polygon       Haidian District             558
   3 │     3  Polygon       Fengtai District             339
   4 │     4  MultiPolygon  Chaoyang District            690
   5 │     5  Polygon       Yanqing District              53
   6 │     6  Polygon       Tongzhou District            321
   7 │     7  Polygon       Shunyi District              266
   8 │     8  Polygon       Pinggu District               81
   9 │     9  Polygon       Miyun District               101
  10 │    10  Polygon       Mentougou District            76
  11 │    11  Polygon       Huairou District              90
  12 │    12  Polygon       Fangshan District            232
  13 │    13  Polygon       Daxing District              393
  14 │    14  Polygon       Changping District           429
  15 │    15  Polygon       Xicheng District             177
  16 │    16  Polygon       Dongcheng District           123

We can verify that about 18% of the target population was not allocated. This result is consistent with the results obtained from allocaiton of individuals to households.

In [26]:
@show sum(unassigned2["unassigned_areas"].:population)
@show sum(aggregated_areas.:population)

sum((unassigned2["unassigned_areas"]).population) = 4031
sum(aggregated_areas.population) = 

21890.0


21890.0

In [25]:
sum(unassigned2["unassigned_areas"].:population) / sum(aggregated_areas.:population)

0.18414801279122886